# Comparação entre modelos

Neste notebook, verificamos o quão próximas da realidade estiveram historicamente as previsões geradas pelos modelos SEIR e SEAPMDR, implementados neste repositório e aplicados a diferentes momentos da epidemia nas Unidades Federativas brasileiras no notebook [`simulation.ipynb`](./simulation.ipynb). Além disso, comparamos o desempenho dos modelos com diferentes antecedências nas previsões (até 90 dias) e em diferentes cenários (bom e ruim).

## Preparar o ambiente

Importar as dependências necessárias.

In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
from sklearn.metrics import mean_squared_error

## Carregar os dados da retroprevisão

Para esta análise, utilizaremos os dados da simulação gerados com o notebook [`simulation.ipynb`](./simulation.ipynb) - guardados localmente no arquivo [`/data/br-states-simulacovid-predictions.csv`](./data/br-states-simulacovid-predictions.csv) - bem como dados de casos retirados do [Brasil.IO](https://brasil.io/dataset/covid19/caso_full/) e tratados pelo [CoronaCidades](https://github.com/ImpulsoGov/coronacidades-datasource/).

### Obter histórico da situação epidemiológica nos estados

Conforme informado no respectivo [dicionário de dados](https://github.com/ImpulsoGov/coronacidades-datasource/blob/master/dictionaries/br_states_cases_full.csv), as colunas presentes no histórico completo de casos nas Unidades da Federação são*: 

Nome da coluna | Descrição
-:- | :--
**active_cases** | **Casos ativos estimados no dia**
cases_mavg (não utilizado) | Média móvel de 7 dias de casos
confirmed_cases | Número de casos confirmados do último dia disponível igual ou anterior à data
daily_cases | Número de novos casos confirmados desde o último dia
daily_cases_growth | Tendência do número de casos por dia (crescendo | decrescendo | estabilizando)
daily_cases_mavg (não utilizado) | Média móvel de 7 dias para casos diários
daily_cases_mavg_100k | Média móvel de 7 dias para casos diários por 100 mil habitantes
deaths | Número de mortes acumuladas do último dia disponível igual ou anterior à data
deaths_mavg (não utilizado) | Média móvel de 7 dias de mortes acumuladas
estimated_cases | Casos novos diários estimados no local
infectious_period_cases | Número de novos casos no período de progressão da doença (até 14 dias antes da data da linha)
**last_updated** | **Data da atualização dos dados* (renomeado de date)**
new_deaths | Número de novos óbitos desde o último dia*
new_deaths_growth | Tendência de número de óbitos por dia (crescendo | decrescendo | estabilizando)
new_deaths_mavg (não utilizado) | Média móvel de 7 dias de novos óbitos 
new_deaths_mavg_100k | Média móvel de 7 dias de novos óbitos por 100 mil habitantes 
notification_rate | Taxa de notificação de casos estimada no município
**population** | **População estimada pelo IBGE em 2019**
**state_id** | **Sigla da unidade federativa**
state_name | Nome do estado
**state_num_id** | **Código numérico do estado (IBGE)**
total_estimated_cases | Casos acumulados estimados no local até a data
data_last_refreshed | Data da última atualização do dado na API

\* Colunas destacadas **em negrito** são mantidas para a análise.

In [2]:
# load cases
cases_url = "http://datasource.coronacidades.org/br/states/cases/full"
df_cases = pd.read_csv(cases_url, usecols=["state_num_id", "state_id", "last_updated", "active_cases", "population"])
df_cases["last_updated"] = pd.to_datetime(df_cases["last_updated"])
df_cases.dropna(inplace=True)

df_cases

active_cases last_updated  population state_id  state_num_id
14           756.0   2020-04-03     1777225       RO            11
15           720.0   2020-04-04     1777225       RO            11
16           885.0   2020-04-05     1777225       RO            11
17          1080.0   2020-04-06     1777225       RO            11
18          1552.0   2020-04-07     1777225       RO            11
...            ...          ...         ...      ...           ...
8724       24231.0   2021-01-07     3015268       DF            53
8725       24185.0   2021-01-08     3015268       DF            53
8726       23271.0   2021-01-09     3015268       DF            53
8727       23649.0   2021-01-10     3015268       DF            53
8728       23427.0   2021-01-11     3015268       DF            53

[7857 rows x 5 columns]

### Obter histórico de previsões para os estados

O arquivo local [`/data/br-states-simulacovid-predictions.csv`](./data/br-states-simulacovid-predictions.csv) contém as estimativas do número de indivíduos em cada compartimento, de acordo com o modelo e o cenário utilizados, última data com dados de entrada para a simulação e o número de dias adiante (até 90):

Nome da coluna | Descrição
-:- | :--
**state_num_id** | **Código numérico do estado (IBGE)**
**model** | **Modelo utilizado para realizar a simulação (`SEIR` ou `SEAPMDR`)**
**scenario** | **Cenário utilizado na simulação (`best`, com a taxa de reprodução constante; ou `worst`, com a taxa dobrando)**
**date_prediction** | **Data de início da simulação**
**days** | **Dias decorridos da data de início da simulação (até 90)**
**S** | **Número de indivíduos suscetíveis na população**
**E** | **Número de indivíduos expostos na população (ainda não tiveram tempo de desenvolver sintomas)**
E0 | Número de indivíduos expostos latentes (não-transmissíveis) na população *(apenas modelo SEAPMDR)*
E1 | Número de indivíduos expostos pré-sintomáticos (transmissíveis) na população *(apenas modelo SEAPMDR)*
**I** | **Número de indivíduos infectados na população**
I0 | Número de indivíduos infectados assintomáticos na população *(apenas modelo SEAPMDR)*
I1 | Número de indivíduos infectados com sintomas moderados na população
I2 | Número de indivíduos infectados com sintomas graves na população (hospitalizados)
I3 | Número de indivíduos infectados em estado crítico na população (hospitalizados em cuidados intensivos)
**R** | **Número de indivíduos recuperados (imunes) na população**
**D** | **Mortes**

\* Colunas destacadas **em negrito** são mantidas para a análise.

In [22]:
# load historical predictions
df_predictions = pd.read_csv("../data/br-states-simulacovid-predictions.csv")
df_predictions["date_prediction"] = pd.to_datetime(df_predictions["date_prediction"])

# fill mission values
df_predictions["E0"] = df_predictions["E0"].fillna(0)
df_predictions["E1"] = df_predictions["E1"].fillna(0)
df_predictions["I0"] = df_predictions["I0"].fillna(0)

# sum up infectious subcompartments
df_predictions["I"] = df_predictions["I0"] + df_predictions["I1"] + df_predictions["I2"] + df_predictions["I3"]

# drop unwanted columns
df_predictions = df_predictions[["state_num_id", "model", "scenario", "date_prediction", "days", "S", "E", "I", "R", "D"]]

df_predictions

state_num_id    model scenario date_prediction  days             S  \
0                  11  SEAPMDR    worst      2020-04-19     1  1.732049e+06   
1                  11  SEAPMDR    worst      2020-04-19     2  1.721016e+06   
2                  11  SEAPMDR    worst      2020-04-19     3  1.706539e+06   
3                  11  SEAPMDR    worst      2020-04-19     4  1.688375e+06   
4                  11  SEAPMDR    worst      2020-04-19     5  1.666062e+06   
...               ...      ...      ...             ...   ...           ...   
2774039            53     SEIR     best      2021-01-19    87  2.211629e+06   
2774040            53     SEIR     best      2021-01-19    88  2.211346e+06   
2774041            53     SEIR     best      2021-01-19    89  2.211070e+06   
2774042            53     SEIR     best      2021-01-19    90  2.210800e+06   
2774043            53     SEIR     best      2021-01-19    91  2.210536e+06   

                    E             I              R             D  
0        37073.552668   7393.000000     705.000000      4.000000  
1        41839.887176  12083.190390    2278.094257      8.262260  
2        48794.782778  17223.430966    4654.920221     12.602302  
3        58087.241606  22838.987462    7906.630186     17.088667  
4        69870.931890  29144.100853   12126.343299     21.831493  
...               ...           ...            ...           ...  
2774039   1624.007466   3379.824970  780147.817428  10929.996403  
2774040   1585.994636   3301.066076  780513.170436  10964.387711  
2774041   1548.859116   3224.108327  780870.002262  10997.984553  
2774042   1512.581241   3148.912147  781218.508181  11030.804718  
2774043   1477.141756   3075.438746  781558.879150  11062.865635  

[2774044 rows x 10 columns]

## Juntar registros do previsto e do observado

Todas as análises seguintes se baseiam na comparação entre o número de casos previstos pelos modelos e o número de casos observados. Para que isso seja possível, juntamos as duas tabelas, usando como colunas comuns o código da Unidade da Federação e a data para a qual foi feita a previsão.

In [23]:
# calculate the date the forecast refers to
df_predictions["reference_date"]=(
    df_predictions.apply(lambda row: row["date_prediction"] + pd.Timedelta(days=row["days"]), axis=1)
)

# merge DataFrame with forecasts to the DataFrame with cases in the correspondent date and state
df_predictions = df_predictions.merge(
    df_cases, how="left", left_on=["state_num_id", "reference_date"], right_on=["state_num_id", "last_updated"]
)

df_predictions

state_num_id    model scenario date_prediction  days             S  \
0                  11  SEAPMDR    worst      2020-04-19     1  1.732049e+06   
1                  11  SEAPMDR    worst      2020-04-19     2  1.721016e+06   
2                  11  SEAPMDR    worst      2020-04-19     3  1.706539e+06   
3                  11  SEAPMDR    worst      2020-04-19     4  1.688375e+06   
4                  11  SEAPMDR    worst      2020-04-19     5  1.666062e+06   
...               ...      ...      ...             ...   ...           ...   
2774039            53     SEIR     best      2021-01-19    87  2.211629e+06   
2774040            53     SEIR     best      2021-01-19    88  2.211346e+06   
2774041            53     SEIR     best      2021-01-19    89  2.211070e+06   
2774042            53     SEIR     best      2021-01-19    90  2.210800e+06   
2774043            53     SEIR     best      2021-01-19    91  2.210536e+06   

                    E             I              R             D  \
0        37073.552668   7393.000000     705.000000      4.000000   
1        41839.887176  12083.190390    2278.094257      8.262260   
2        48794.782778  17223.430966    4654.920221     12.602302   
3        58087.241606  22838.987462    7906.630186     17.088667   
4        69870.931890  29144.100853   12126.343299     21.831493   
...               ...           ...            ...           ...   
2774039   1624.007466   3379.824970  780147.817428  10929.996403   
2774040   1585.994636   3301.066076  780513.170436  10964.387711   
2774041   1548.859116   3224.108327  780870.002262  10997.984553   
2774042   1512.581241   3148.912147  781218.508181  11030.804718   
2774043   1477.141756   3075.438746  781558.879150  11062.865635   

        reference_date  active_cases last_updated  population state_id  
0           2020-04-20        7470.0   2020-04-20   1777225.0       RO  
1           2020-04-21        7639.0   2020-04-21   1777225.0       RO  
2           2020-04-22        7978.0   2020-04-22   1777225.0       RO  
3           2020-04-23        8726.0   2020-04-23   1777225.0       RO  
4           2020-04-24        8390.0   2020-04-24   1777225.0       RO  
...                ...           ...          ...         ...      ...  
2774039     2021-04-16           NaN          NaT         NaN      NaN  
2774040     2021-04-17           NaN          NaT         NaN      NaN  
2774041     2021-04-18           NaN          NaT         NaN      NaN  
2774042     2021-04-19           NaN          NaT         NaN      NaN  
2774043     2021-04-20           NaN          NaT         NaN      NaN  

[2774044 rows x 15 columns]

## Exemplos de curvas de casos - previsto e observado

Como passo inicial para entender como os modelos se comportam em relação à realidade, podemos fixar uma data e um território e acompanhar como a curva de casos previstos em cada um dos modelos e cenários se compara com o que aconteceu depois.

### Definir visualização

Definimos uma função para encapsular o processo de gerar uma visualização dos casos previstos e observados em uma Unidade da Federação (ou no conjunto delas) ao longo dos três meses seguintes a uma data qualquer. Assim, torna-se mais fácil visualizar qualquer data e UF de interesse, sem maiores modificações no código.

In [56]:
def viz_case_evolution(uf="BR", date_start="2020-05-01", date_end=None, plot=True, **kwargs):
    """Visualize the evolution of predicted and observed active cases.
    
    Parameters:
        uf (str): Abbreviation of a brazilian state, or 'BR' for the
            country-level aggregate (default).
        date_start (str): `pandas.Timestamp` parseable string with the day 0
            of the time-series (defaults to '2020-05-01').
        date_start (str): an optional `pandas.Timestamp` parseable string 
            with the last day of the time-series (defaults to None).
        plot (bool): whether to display the plot to the console (default). If
            false, returns the DataFrame with the data.
        **kwargs: extra keyword arguments to be passed to `px.line()` function.
    
    Returns:
        None, if ``plot=True``; or a `pd.DataFrame` with the plot, if
        ``plot=False``.
    """

    date_start = pd.Timestamp(date_start)
    df = df_predictions.copy()
    df = df.query("date_prediction == @date_start")
    if date_end:
        date_end = pd.Timestamp(date_end)
        df = df.query("last_updated <= @date_end")
    if uf == "BR":
        df = (
            df
            .groupby(["model", "scenario", "last_updated"])
            .sum()
            .drop(columns=["state_num_id"])
            .reset_index()
        )
    else:
        df = df.query("state_id == @uf")
    
    # turn predictions into rows
    df = df.melt(
        id_vars=["model", "scenario", "last_updated"],
        value_vars=["I", "active_cases"],
        var_name="value_type",
        value_name="cases",
    ).rename(columns={"last_updated": "date"})
    df.loc[df["value_type"]=="active_cases", "model"] = "Observado"
    df = df.drop_duplicates().drop(columns=["value_type"])
    
    # Rename scenarios to portuguese
    df["scenario"] = df["scenario"].apply(lambda scen: "melhor" if scen == "best" else "pior")
    
    # Convert date boundaries to strings (to figure in the plot's title)
    date_start_str = date_start.strftime("%d/%m/%Y")
    if date_end:
        date_end_str = date_end.strftime("%d/%m/%Y")
    else:
        date_end_str = df["date"].max().strftime("%d/%m/%Y")
    
    # prepare plot
    fig = px.line(
        df,
        x="date",
        y="cases",
        color="model",
        facet_col="scenario",
        title=f"{uf} - Casos previstos X observados ({date_start_str} - {date_end_str})",
        labels={
            "date": "Dias",
            "cases": "Casos ativos",
            "model": "Modelo",
            "scenario": "Cenário",
        },
        **kwargs
    )
    
    # display to console or return DataFrame
    if plot:
        fig.show()
        del df
    else:
        return df

### Exemplo 1: Casos previstos e observados - Brasil, mai.-dez./2020 

**ATENÇÃO**: As escalas dos gráficos diferem entre si.

In [57]:
viz_case_evolution(uf="BR", date_start="2020-05-01", plot=True)

In [58]:
viz_case_evolution(uf="BR", date_start="2020-08-01", plot=True)

In [59]:
viz_case_evolution(uf="BR", date_start="2020-11-01", date_end="2020-12-31", plot=True)

### Exemplo 2: Casos preditos e observados - Espírito Santo, mai.-dez./2020

**ATENÇÃO**: As escalas dos gráficos diferem entre si.

In [60]:
viz_case_evolution(uf="ES", date_start="2020-05-01", plot=True)

In [62]:
viz_case_evolution(uf="ES", date_start="2020-08-01", plot=True)

In [61]:
viz_case_evolution(uf="ES", date_start="2020-11-01", date_end="2020-12-31", plot=True)

## Desempenho consolidado dos modelos

Pará além da visualização de como os modelos se comportam para uma ou outra UF e período, uma comparação geral da qualidade dos modelos pode fazer uso de métricas específicas para medir a adequação dos valores previstos ao histórico observado.

Nesta seção, utilizaremos as retroprojeções para medir e visualizar os erros (resíduos de cada um dos modelos).

### Calcular o número de casos per capita

Utilizaremos as retroprojeções para estimar a qualidade de ambos os modelos em análise.

In [36]:
# filter dataset
df_residuals = df_predictions[
    ["state_num_id", "state_id", "model", "scenario", "reference_date", "days", "I", "active_cases", "population"]
].dropna()

# calculate per capita predicted and observed cases
df_residuals["predicted_percapita"] = df_residuals["I"] / df_residuals["population"]
df_residuals["observed_percapita"] = df_residuals["active_cases"] / df_residuals["population"]
df_residuals.drop(columns=["I", "active_cases", "population"], inplace=True)

# calculate residuals
df_residuals["residuals_percapita"] = (
    df_residuals["predicted_percapita"] - df_residuals["observed_percapita"]
)
df_residuals["residuals_perK"] = df_residuals["residuals_percapita"] * 10**3

df_residuals

state_num_id state_id    model scenario reference_date  days  \
0                  11       RO  SEAPMDR    worst     2020-04-20     1   
1                  11       RO  SEAPMDR    worst     2020-04-21     2   
2                  11       RO  SEAPMDR    worst     2020-04-22     3   
3                  11       RO  SEAPMDR    worst     2020-04-23     4   
4                  11       RO  SEAPMDR    worst     2020-04-24     5   
...               ...      ...      ...      ...            ...   ...   
2770314            53       DF     SEIR     best     2021-01-11     2   
2770404            53       DF  SEAPMDR    worst     2021-01-11     1   
2770495            53       DF  SEAPMDR     best     2021-01-11     1   
2770586            53       DF     SEIR    worst     2021-01-11     1   
2770677            53       DF     SEIR     best     2021-01-11     1   

         predicted_percapita  observed_percapita  residuals_percapita  \
0                   0.004160            0.004203            -0.000043   
1                   0.006799            0.004298             0.002501   
2                   0.009691            0.004489             0.005202   
3                   0.012851            0.004910             0.007941   
4                   0.016399            0.004721             0.011678   
...                      ...                 ...                  ...   
2770314             0.005999            0.007769            -0.001771   
2770404             0.008354            0.007769             0.000585   
2770495             0.008354            0.007769             0.000585   
2770586             0.005848            0.007769            -0.001921   
2770677             0.005848            0.007769            -0.001921   

         residuals_perK  
0             -0.043326  
1              2.500635  
2              5.202172  
3              7.941025  
4             11.677813  
...                 ...  
2770314       -1.770751  
2770404        0.585023  
2770495        0.585023  
2770586       -1.921322  
2770677       -1.921322  

[2241876 rows x 10 columns]

### Visualizar resíduos

A visualização da distribuição dos resíduos permite identificar se cada modelo tem alguma tendência especial a subestimar ou superestimar o valor real do número de casos, e como esses resíduos variam quando se aumenta o números de dia de antecedência com que a previsão é feita.

O gráfico a seguir utiliza *boxplots* para evidenciar a tendência central e a dispersão dos resíduos em relação ao observado (uma previsão certeira é a que tem valor 0 no eixo vertical). A dispersão é expressa em termos do [intervalo inter-quartílico (IQR)](https://pt.wikipedia.org/wiki/Amplitude_interquartil), demonstrado visualmente pela caixa no centro dos *boxplots*. Já a tendência central é indicada pela mediana (valor acima e abaixo do qual se encontram 50% das observações), representada risco no meio dos *boxplots*.

Conforme o esperado, a dispersão dos resíduos é maior quanto maior é o intervalo entre a simulação e a data cujo número de casos se tenta prever - indicando que os modelos tendem a cometer mais erros extremos, para mais e para menos, quando são utilizados para prever a situação epidemiológica daqui a vários meses. No entanto, essa tendência é significativamente maior no modelo SEIR do que no SEAPMDR, indicando que o modelo SEAPMDR pode ser preferível quando se trata de previsões em prazos mais longos.

Quanto à tendência central e a posição do primeiro e terceiro quartis (extremos da "caixa" do *boxplot*), esses demonstram que o modelo SEAPMDR têm uma tendência maior do que o modelo SEIR a **subestimar** o número de casos. Nas previsões de mais curto prazo (15 e 30 dias), a mediana do modelo SEIR se encontra mais próxima ao zero, ao passo que, a partir daí, tende cada vez mais à parte superior do gráfico - o que denota uma tendência à superestimativa dos casos.

In [38]:
fig = px.box(
    df_residuals.query("scenario=='best' and (days % 15 == 0)"),
    x="days",
    y="residuals_perK",
    color="model",
    title="Perfil dos resíduos (melhor cenário)",
    labels={
        "model": "Modelo",
        "residuals_perK": "Resíduo<br>(casos previstos - observados,<br>por mil de habitantes)",
        "days": "Dias de antecedência da previsão"
    }
)

fig.show()

### Raíz do Erro Quadrático Médio

Uma outra maneira de avaliar a qualidade geral dos modelos é por meio da [raíz do erro quadrático médio (RMSE)](https://en.wikipedia.org/wiki/Root-mean-square_deviation), uma métrica tradicional para comparar modelos com variáveis-resposta numéricas.

A raíz do erro quadrático médio é um número sempre positivo, que expressa os resíduos não explicados pelo modelo. A escala de saída é igual à de entrada - neste caso, em casos ativos per mil habitantes. Um RMSE igual a zero indica que o modelo é perfeito - todas as suas previsões são idênticas ao observado.

No gráfico abaixo, o RMSE dos modelos SEIR e SEAPMDR é expresso como uma função do número de dias entre a simulação e a data cujo número de casos o modelo tentou prever. 

In [46]:
def rmse( g ):
    """Generates RMSE values for a pd.DataFrame."""
    # CREDIT: https://stackoverflow.com/a/47914634
    # TODO: abstract column names
    rmse = np.sqrt(mean_squared_error( g["observed_perK"], g["predicted_perK"] ) )
    return pd.Series(rmse)

df_residuals["observed_perK"] = df_residuals["observed_percapita"] * 10**3
df_residuals["predicted_perK"] = df_residuals['predicted_percapita'] * 10**3
performance = (
    df_residuals
    .groupby(["model", "days", "scenario"])
    .apply(rmse)
    .rename(columns={0:"rmse"})
    .reset_index()
)

# Rename scenarios to portuguese
performance["scenario"] = performance["scenario"].apply(lambda scen: "melhor" if scen == "best" else "pior")

In [48]:
fig = px.line(
    performance.query("days < 91 & days % 2"),
    x="days",
    y="rmse",
    color="model",
    facet_col = "scenario",
    title="Raíz do Erro Quadrático Médio para modelos SEIR e SEAPMDR",
    labels={
        "model": "Modelo",
        "days": "Dias de antecedência da previsão",
        "rmse": "RMSE",
        "scenario": "Cenário"
    }
)

fig.show()